# 1M_recipes dataset word2vec experiments

In [1]:
import numpy as np
import json

import nltk
from nltk.stem import PorterStemmer
from nltk.stem import LancasterStemmer
from nltk.corpus import stopwords as nltk_stopwords

from pprint import pprint

from gensim.test.utils import common_texts, get_tmpfile
from gensim.models import Word2Vec

from json_buffered_reader import JSON_buffered_reader as JSON_br

import pandas as pd

import settings

In [2]:
from ipypb import track

In [3]:
from IPython.display import HTML, Markdown

* reading firs n recipes from json stream

In [4]:
n = 1000000

In [5]:
buffered_reader = JSON_br(settings.one_million_recipes_file)

In [6]:
instructions = []

----

In [7]:
stopwords = set(nltk_stopwords.words('english'))
sentence_symbols = set(('.', ';', '!', '?', ',')) 
porter = PorterStemmer()
model = None

stemmed_stopwords = set([porter.stem(word) for word in stopwords])

def recipe2instructions(stream_item):
    return [t['text'] for t in stream_item['instructions']]

def stemmed_recipe_instruction(json_item, stemmer = porter):
    item_instructions = recipe2instructions(json_item)
    stemmed_list = []
    for instruction in item_instructions:
        stemmed_list.append([stemmer.stem(i).lower() for i in nltk.word_tokenize(instruction)])
    
    result = []
    for stemmed in stemmed_list:
        stemmed_without_stopwords = []
        for word in stemmed:
            if (word not in stopwords) and (word not in sentence_symbols):
                stemmed_without_stopwords.append(word)
        result.append(stemmed_without_stopwords)
    
    return  result


* example:

In [8]:
#item = buffered_reader.__next__()

In [9]:
#stemmed_recipe_instruction(item)

* reading up to n recipes:

In [10]:

for i in track(range(n)):
    try:
        json_recipe = buffered_reader.__next__()
    except StopIteration:
        print("reached end of stream after " + i + "iterations")
        break
    instructions += stemmed_recipe_instruction(json_recipe)
    #print(i)


 [████████████████████████████████████████████████████████████] 1000000/1000000 [01:01:03<00:00, 0.00s/it]

* train word2vec on that instructions

In [11]:
model = Word2Vec(instructions, size=512, window=1, min_count=3, workers=4)
def word_similarity(word_a:str, word_b:str, model=model, stemmer=porter):
    return model.wv.similarity(stemmer.stem(word_a), stemmer.stem(word_b))

def word_exists(word:str, model=model, stemmer=porter):
    return stemmer.stem(word) in model.wv


In [12]:
word_similarity("dice", "onions")

0.46360567

In [13]:
path = get_tmpfile("wordvectors.kv")

In [14]:
model.wv.save(path)

In [15]:
model.wv.most_similar_to_given("mash", ["salad","potato", "oil", "tomato"])

'potato'